In [2]:
import trimesh
import numpy as np
import os
import plotly.graph_objects as go

class Modelo3D:
    """Clase para representar y manejar un modelo 3D"""

    def __init__(self, ruta):
        self.ruta = ruta
        self.nombre = os.path.basename(ruta)
        self.malla = self._cargar_malla()

    def _cargar_malla(self):
        """Carga el modelo desde archivo"""
        try:
            data = trimesh.load(self.ruta)
            if isinstance(data, trimesh.Scene):
                return trimesh.util.concatenate(data.geometry.values())
            return data
        except Exception as e:
            print(f"❌ Error al cargar {self.nombre}: {e}")
            return None

    def info_basica(self):
        """Devuelve información estructural clave del modelo"""
        if not self.malla:
            return None
        v = len(self.malla.vertices)
        f = len(self.malla.faces)
        cerrado = self.malla.is_watertight
        bbox = self.malla.bounding_box.extents
        volumen = self.malla.volume if self.malla.is_volume else None
        duplicados = v - len(np.unique(self.malla.vertices, axis=0))
        return dict(
            nombre=self.nombre,
            vertices=v,
            caras=f,
            duplicados=duplicados,
            cerrado=cerrado,
            bbox=tuple(bbox),
            volumen=volumen
        )

    def exportar(self, carpeta_salida, formatos=('obj', 'stl', 'glb')):
        """Exporta a múltiples formatos"""
        if not self.malla:
            return
        nombre_base = os.path.splitext(self.nombre)[0]
        for fmt in formatos:
            salida = os.path.join(carpeta_salida, f"{nombre_base}.{fmt}")
            try:
                self.malla.export(salida)
                print(f"📤 Exportado: {salida}")
            except Exception as e:
                print(f"❌ Error exportando {fmt}: {e}")

    def mostrar(self):
        """Visualización 3D interactiva con Plotly"""
        if not self.malla:
            return
        v, f = self.malla.vertices, self.malla.faces
        fig = go.Figure(data=[
            go.Mesh3d(
                x=v[:,0], y=v[:,1], z=v[:,2],
                i=f[:,0], j=f[:,1], k=f[:,2],
                color='lightblue', opacity=0.5
            )
        ])
        fig.update_layout(title=self.nombre, scene=dict(aspectmode='data'))
        fig.show()


class AnalizadorLote:
    """Procesa varios modelos a la vez"""

    def __init__(self, carpeta):
        self.carpeta = carpeta
        self.modelos = self._cargar_todos()

    def _cargar_todos(self):
        """Carga todos los modelos válidos de una carpeta"""
        modelos = []
        for archivo in os.listdir(self.carpeta):
            if archivo.lower().endswith(('.obj', '.stl', '.glb', '.gltf')):
                modelo = Modelo3D(os.path.join(self.carpeta, archivo))
                if modelo.malla:
                    modelos.append(modelo)
        return modelos

    def mostrar_resumen(self):
        """Imprime tabla comparativa entre modelos"""
        print("\n📊 Resumen comparativo:\n")
        header = f"{'Nombre':<20} | {'Verts':<6} | {'Caras':<6} | {'Dup':<4} | {'Cerrado':<8} | {'Volumen':<10}"
        print(header)
        print('-'*len(header))
        for m in self.modelos:
            props = m.info_basica()
            vol = f"{props['volumen']:.2f}" if props['volumen'] else 'N/A'
            print(f"{props['nombre']:<20} | {props['vertices']:<6} | {props['caras']:<6} | {props['duplicados']:<4} | {'Sí' if props['cerrado'] else 'No':<8} | {vol:<10}")

    def exportar_todos(self, carpeta_destino):
        """Convierte todos los modelos cargados"""
        for modelo in self.modelos:
            modelo.exportar(carpeta_destino)

    def visualizar_todos(self):
        """Muestra todos los modelos uno por uno"""
        for modelo in self.modelos:
            modelo.mostrar()

if __name__ == "__main__":
    ruta_modelos = "../datos/"
    ruta_salida = "../resultados/python/modelos"

    lote = AnalizadorLote(ruta_modelos)
    lote.mostrar_resumen()
    lote.visualizar_todos()
    lote.exportar_todos(ruta_salida)



📊 Resumen comparativo:

Nombre               | Verts  | Caras  | Dup  | Cerrado  | Volumen   
---------------------------------------------------------------------
piggyGLB.glb         | 37720  | 71858  | 1773 | No       | N/A       
piggyOBJ.obj         | 36818  | 71858  | 871  | No       | N/A       
piggySTL.stl         | 35947  | 71858  | 0    | Sí       | 0.70      


📤 Exportado: ../resultados/python/modelos\piggyGLB.obj
📤 Exportado: ../resultados/python/modelos\piggyGLB.stl
📤 Exportado: ../resultados/python/modelos\piggyGLB.glb
📤 Exportado: ../resultados/python/modelos\piggyOBJ.obj
📤 Exportado: ../resultados/python/modelos\piggyOBJ.stl
📤 Exportado: ../resultados/python/modelos\piggyOBJ.glb
📤 Exportado: ../resultados/python/modelos\piggySTL.obj
📤 Exportado: ../resultados/python/modelos\piggySTL.stl
📤 Exportado: ../resultados/python/modelos\piggySTL.glb
